In [1]:
import pandas as pd
import numpy as np
from sklearn.cluster import KMeans

In [2]:
offers = pd.read_excel('WineKMCOfferinformation.xlsx')

In [3]:
offers.head()

Offer #  Campaign            Varietal  Minimum Qty (kg)  Discount (%)  \
0        1   January              Malbec                72            56   
1        2   January          Pinot Noir                72            17   
2        3  February           Espumante               144            32   
3        4  February           Champagne                72            48   
4        5  February  Cabernet Sauvignon               144            44   

        Origin  Past Peak  
0       France      False  
1       France      False  
2       Oregon       True  
3       France       True  
4  New Zealand       True

In [4]:
trans = pd.read_excel('WineKMCTransactions.xlsx')

In [5]:
trans.head()

Customer Last Name  Offer #
0              Smith        2
1              Smith       24
2            Johnson       17
3            Johnson       24
4            Johnson       26

# 1. Объедиение данных

In [6]:
data = trans.merge(offers, how = 'left')

In [7]:
data

Customer Last Name  Offer #   Campaign            Varietal  \
0                Smith        2    January          Pinot Noir   
1                Smith       24  September          Pinot Noir   
2              Johnson       17       July          Pinot Noir   
3              Johnson       24  September          Pinot Noir   
4              Johnson       26    October          Pinot Noir   
..                 ...      ...        ...                 ...   
319             Fisher       11        May           Champagne   
320             Fisher       22     August           Champagne   
321             Fisher       28   November  Cabernet Sauvignon   
322             Fisher       30   December              Malbec   
323             Fisher       31   December           Champagne   

     Minimum Qty (kg)  Discount (%)     Origin  Past Peak  
0                  72            17     France      False  
1                   6            34      Italy      False  
2                  12            47    Germany      False  
3                   6            34      Italy      False  
4                 144            83  Australia      False  
..                ...           ...        ...        ...  
319                72            85     France      False  
320                72            63     France      False  
321                12            56     France       True  
322                 6            54     France      False  
323                72            89     France      False  

[324 rows x 8 columns]

In [8]:
trans['flag'] = 1

#2. ![cluster_0-1.png](![cluster_0_001.png](cluster_0_001.png))Создание матрицы "Клиент - Заказ"

In [9]:
clients_offers = pd.pivot_table(trans, index = 'Customer Last Name', columns =['Offer #'], values = 'flag', fill_value = 0)

In [10]:
clients_offers

Offer #             1   2   3   4   5   6   7   8   9   10  ...  23  24  25  \
Customer Last Name                                          ...               
Adams                0   0   0   0   0   0   0   0   0   0  ...   0   0   0   
Allen                0   0   0   0   0   0   0   0   1   0  ...   0   0   0   
Anderson             0   0   0   0   0   0   0   0   0   0  ...   0   1   0   
Bailey               0   0   0   0   0   0   1   0   0   0  ...   0   0   0   
Baker                0   0   0   0   0   0   1   0   0   1  ...   0   0   0   
...                 ..  ..  ..  ..  ..  ..  ..  ..  ..  ..  ...  ..  ..  ..   
Williams             0   0   0   0   0   0   0   0   0   0  ...   0   0   0   
Wilson               0   0   0   0   0   0   0   1   0   0  ...   0   0   0   
Wood                 1   0   0   0   0   0   0   0   0   1  ...   0   0   0   
Wright               0   0   0   1   0   1   0   0   0   0  ...   0   0   0   
Young                0   0   0   0   0   1   0   0   1   0  ...   0   0   0   

Offer #             26  27  28  29  30  31  32  
Customer Last Name                              
Adams                0   0   0   1   1   0   0  
Allen                0   1   0   0   0   0   0  
Anderson             1   0   0   0   0   0   0  
Bailey               0   0   0   0   1   0   0  
Baker                0   0   0   0   0   1   0  
...                 ..  ..  ..  ..  ..  ..  ..  
Williams             0   0   0   0   0   1   0  
Wilson               0   0   0   0   1   0   0  
Wood                 0   0   0   0   0   1   0  
Wright               0   1   0   0   0   0   0  
Young                0   0   0   0   0   1   1  

[100 rows x 32 columns]

# 3. Изменение типов данных

In [26]:
data['Past Peak'] = data['Past Peak'].apply(lambda x: 'True' if x == True else 'False')

In [27]:
data['Offer #'] = data['Offer #'].apply(lambda x: str(x))

# 4. Функция "Кластеризация и рисование графиков"

In [41]:
def train(clusters, clients_offers):

      """ выбор количества кластеров и обучение модели """

      c = KMeans(n_clusters=clusters).fit(clients_offers)
      clusterisation = pd.concat([pd.DataFrame(clients_offers.index), pd.DataFrame(c.labels_)], axis= 1 )
      return clusterisation

def creation(clusters, clients_offers, data):

    """ Разделение первоначального датасета, создание графиков по каждому кластеру """

    for i in range(clusters):
          clusterisation = train(clusters, clients_offers)
          cluster_tec = data[data['Customer Last Name'].isin(list(clusterisation[clusterisation.iloc[:, 1] == i]['Customer Last Name']))]
          cluster_info(cluster_tec, i)


def cluster_info (cluster, num):

    """ Рисование графиков """

    pdf = PdfPages(f'cluster_{num}.pdf')
    fig, axs = plt.subplots(nrows=(len(cluster.columns))//2 + (len(cluster.columns)) % 2, ncols=2, figsize=(100, 100))
    plt.rcParams['font.size'] = '40'
    plt.subplots_adjust(hspace = 0.5)
    for idx, column in enumerate(cluster.columns):
        ax = axs[idx//2][idx%2]
        ax.tick_params(labelsize=40)
        if cluster[column].dtype == 'object':
            cluster[column].value_counts().plot(kind='bar', color='skyblue', ax=ax)
            ax.set_title(f'Столбчатая диаграмма для {column}')
            ax.set_xlabel('Категории')
            ax.set_ylabel('Частота')
        else:
            ax.hist(cluster[column], bins = 20, color='lightcoral', edgecolor='black')
            ax.set_title(f'Гистограмма для {column}')
            ax.set_xlabel('Значения')
            ax.set_ylabel('Частота')

    pdf.savefig(fig)
    pdf.close()

In [37]:
import matplotlib.pyplot as plt
from matplotlib.backends.backend_pdf import PdfPages

In [ ]:
creation(3, clients_offers, data)

# 5. Анализ разделения на 3 кластера

**Cluster 1**

![alt text](https://drive.google.com/uc?id=1Zcj9lQ_W7hemperaSwn2Kk1u6yELIZGs)

Опишем клиентов из кластера 1.

*   Самым частым покупателем в кластере является Сандерс.
*   Самые частовстречающиеся заказы среди клиентов 1 кластера - 22 и 31.
*   Самый популярный период сбора - Август, а также Декабрь (по этому критерию нет четкого деления).
*   Самый популярный вид - Champagne (здесь есть четко выраженное деление, у Champagne большой отрыв от остальных видов).
*   Клиенты 1 кластера берут продукт большими партиями от 60 кг (четко выраженный критерий).
*   По скидкам можно сказать, что клиенты 1 кластера предпочитают большие скидки, но это в силу того, что они берут большие партии.
*   Страна производства - с большим отрывом Франция.
*   Предпочитают не поздний сбор.

**Итог** - 1 кластер - клиенты, покупающие французское Шампанское большими партиями. Любят скидки, так как берут большие партии, предпочитают шампанское августа и декабря, не позднего сбора.


**Cluster 2**

![alt text](https://drive.google.com/uc?id=1a6gROvKsI89VPF70Dao64d6cvVHOvCLF)

Опишем клиентов из кластера 2.

*   Самым частым покупателем в кластере является Петерсон.
*   Самые частовстречающиеся заказы среди клиентов 1 кластера - 24 и 26.
*   Самый популярный период сбора - Сентябрь, а также Октябрь (по этому критерию нет четкого деления). Клиенты предпочитают продукты осеннего производства.
*   Самый популярный вид - Pinot Noir (здесь есть четко выраженное деление).
*   Клиенты 1 кластера берут продукт и маленькими, и большими партиями.
*   Страна производства - разная.
*   Предпочитают исключительно не поздний сбор.

**Итог** - 2 кластер - клиенты, покупающие осенний Pino Noir. Партии берут и маленькие, и большие. Разной страны производства. В этом кластере гораздо меньше определенности, чем в 1.


**Cluster 3**

![alt text](https://drive.google.com/uc?id=1e1o6w_uU-rtDboGMrYm7E2bjSkCWsbmS)

Опишем клиентов из кластера 3.

*   Самым частым покупателем в кластере является Хеджес.
*   Самые частовстречающиеся заказы среди клиентов 1 кластера - 29 и 30.
*   Самый популярный период сбора - Март.
*   Самый популярный вид - Espumante (но другие виды в этом кластере тоже покупают).
*   Клиенты 1 кластера берут продукт маленькими партиями (четко выраженный критерий).
*   Страна производства - с отрывом Франция.
*   Предпочитают не поздний сбор.

**Итог** - 3 кластер - клиенты, покупающие Espumante, но не только, маленькими партиями из Франции. Преедпочитают мартовский не поздний сбор.
